# Final Project
#### CSCI 608
#### Jacob Dodson

In [45]:
import pandas as pd
import altair as alt
import numpy as np

from sklearn.linear_model import LogisticRegression
from sklearn.metrics import log_loss
from sklearn.model_selection import KFold, RandomizedSearchCV, GridSearchCV
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline

### **<u>Problem Formulation:</u>**

#### ***1. Descriptive Question:*** What are the overall patterns of academic performance (G3) in Math and Portuguese, and how many students fall into “at-risk” performance categories (G3 < 10)?

#### ***2. Exploratory Question:*** Which external student factors, such as study time, family support, or alcohol use, show the strongest relationships with being academically at risk (G3 < 10)?

#### ***3. Predictive Question:*** Can we build a regression model that predicts whether a student is at risk of failing (G3 < 10) without using G1 or G2, based only on demographic, behavioral, and/or family features?

#### ***4. Inferential Question:*** Do students with strong family support, measured through high family relationship quality (famrel), parental cohabitation (Pstatus), and family educational support (famsup), have significantly higher final grades (G3) compared to students with weaker support, based on bootstrap confidence intervals?

### **<u>Data Collection:</u>**

#### Data was collected from this link: [Student Performance](https://archive.ics.uci.edu/dataset/320/student+performance) which is a Protuguese student performance dataset from students in secondary education (high school).

#### The datasets combines objective school records such as grades (G1, G2, G3) and absences, with a range of self-reported questionnaire data, including demographic, behavioral, family, educational support, and social/emotional variables.

### **<u>Data Preparation:</u>**

In [2]:
mat = pd.read_csv("student-mat.csv", sep=";")
por = pd.read_csv("student-por.csv", sep=";")

In [3]:
mat.head()

school sex  age address famsize Pstatus  Medu  Fedu     Mjob      Fjob  ...  \
0     GP   F   18       U     GT3       A     4     4  at_home   teacher  ...   
1     GP   F   17       U     GT3       T     1     1  at_home     other  ...   
2     GP   F   15       U     LE3       T     1     1  at_home     other  ...   
3     GP   F   15       U     GT3       T     4     2   health  services  ...   
4     GP   F   16       U     GT3       T     3     3    other     other  ...   

  famrel freetime  goout  Dalc  Walc health absences  G1  G2  G3  
0      4        3      4     1     1      3        6   5   6   6  
1      5        3      3     1     1      3        4   5   5   6  
2      4        3      2     2     3      3       10   7   8  10  
3      3        2      2     1     1      5        2  15  14  15  
4      4        3      2     1     2      5        4   6  10  10  

[5 rows x 33 columns]

#### Math dataset has 395 student performance observations

In [4]:
por.head()

school sex  age address famsize Pstatus  Medu  Fedu     Mjob      Fjob  ...  \
0     GP   F   18       U     GT3       A     4     4  at_home   teacher  ...   
1     GP   F   17       U     GT3       T     1     1  at_home     other  ...   
2     GP   F   15       U     LE3       T     1     1  at_home     other  ...   
3     GP   F   15       U     GT3       T     4     2   health  services  ...   
4     GP   F   16       U     GT3       T     3     3    other     other  ...   

  famrel freetime  goout  Dalc  Walc health absences  G1  G2  G3  
0      4        3      4     1     1      3        4   0  11  11  
1      5        3      3     1     1      3        2   9  11  11  
2      4        3      2     2     3      3        6  12  13  12  
3      3        2      2     1     1      5        0  14  14  14  
4      4        3      2     1     2      5        0  11  13  13  

[5 rows x 33 columns]

#### Portuguese dataset has 649 student performance observations

#### Both datasets are tidy. Each row corresponds to one student in a specific course and each column represents a single variable showing we have exactly one observation per row.

### **<u>Analysis:</u>**

#### ***1. Descriptive and Exploratory (data visualizations):***

In [5]:
mat_g3_mean = mat["G3"].mean()
por_g3_mean = por["G3"].mean()

In [6]:
mat_g3_median = mat["G3"].median()
por_g3_median = por["G3"].median()

In [7]:
mat_g3_counts = mat["G3"].value_counts().sort_index()
por_g3_counts = por["G3"].value_counts().sort_index()

In [8]:
mat_at_risk_count = (mat["G3"] < 10).sum()
por_at_risk_count = (por["G3"] < 10).sum()

In [9]:
mat_total = len(mat)
por_total = len(por)

In [10]:
mat_at_risk_pct = mat_at_risk_count / mat_total * 100
por_at_risk_pct = por_at_risk_count / por_total * 100

**Math (G3) Performance Stats**

In [11]:
print(f"Mean G3:, {mat_g3_mean:.2f}")

Mean G3:, 10.42


In [12]:
print(f"Median G3:, {mat_g3_median:.2f}")

Median G3:, 11.00


In [13]:
print("Distribution of G3")
mat_g3_counts

Distribution of G3


G3
0     38
4      1
5      7
6     15
7      9
8     32
9     28
10    56
11    47
12    31
13    31
14    27
15    33
16    16
17     6
18    12
19     5
20     1
Name: count, dtype: int64

In [14]:
print(f"At-risk math students (G3 < 10): {mat_at_risk_count}/{mat_total} " f"({mat_at_risk_pct:.1f}%)")

At-risk math students (G3 < 10): 130/395 (32.9%)


**Portuguese (G3) Performance Stats**

In [15]:
print(f"Mean G3:, {por_g3_mean:.2f}")

Mean G3:, 11.91


In [16]:
print(f"Median G3:, {por_g3_median:.2f}")

Median G3:, 12.00


In [17]:
print("Distribution of G3")
por_g3_counts

Distribution of G3


G3
0      15
1       1
5       1
6       3
7      10
8      35
9      35
10     97
11    104
12     72
13     82
14     63
15     49
16     36
17     29
18     15
19      2
Name: count, dtype: int64

In [18]:
print(f"At-risk Portuguese students (G3 < 10): {por_at_risk_count}/{por_total} " f"({por_at_risk_pct:.1f}%)")

At-risk Portuguese students (G3 < 10): 100/649 (15.4%)


In [19]:
mat['subject'] = 'Math'
por['subject'] = 'Portuguese'

In [20]:
df_plot = pd.concat([mat, por], ignore_index=True)

overlap_hist = alt.Chart(df_plot).mark_bar(opacity=0.5).encode(
    x=alt.X("G3:Q", bin=alt.Bin(maxbins=20), title="Final Grade (G3)"),
    y=alt.Y("count()", title="Count"),
    color=alt.Color("subject:N", title="Subject"),
    tooltip=["subject", "G3"]
).properties(
    width=800,
    height=600,
    title="Overlapped Distribution of Final Grades (G3): Math vs Portuguese"
)
cutoff_df = pd.DataFrame({"cutoff": [10]})

cutoff_line = alt.Chart(cutoff_df).mark_rule(
    color="black",
    strokeWidth=4,
    strokeDash=[6,4]
).encode(
    x="cutoff:Q"
)
hist_chart = overlap_hist + cutoff_line
hist_chart

alt.LayerChart(...)

In [21]:
df_ar = pd.concat([mat, por], ignore_index=True)
df_ar["at_risk"] = df_ar["G3"] < 10
df_ar["at_risk_int"] = df_ar["at_risk"].astype(int)

In [22]:
study_risk = alt.Chart(df_ar).transform_aggregate(
    at_risk_rate='mean(at_risk_int)',
    groupby=['studytime']
).mark_line().encode(
    x=alt.X('studytime:O', title='Study Time Level (1–4)'),
    y=alt.Y('at_risk_rate:Q', title='Proportion At-Risk', axis=alt.Axis(format='%')),
    tooltip=['studytime:O', alt.Tooltip('at_risk_rate:Q', format='.1%')]
).properties(
    width=600,
    height=400,
    title='Proportion of At-Risk Students by Study Time'
)
study_risk

alt.Chart(...)

In [23]:
study_time = alt.Chart(df_ar).transform_aggregate(
    at_risk_rate='mean(at_risk_int)',
    groupby=['studytime']
).mark_line(point=True).encode(
    x=alt.X('studytime:O', title='Study Time (1–5)'),
    y=alt.Y('at_risk_rate:Q', title='Proportion At-Risk', axis=alt.Axis(format='%')),
    tooltip=['studytime:O', alt.Tooltip('at_risk_rate:Q', format='.1%')]
).properties(
    width=600,
    height=400,
    title='Proportion At-Risk by Study Time'
)
study_time

alt.Chart(...)

In [24]:
famrel_risk = alt.Chart(df_ar).transform_aggregate(
    at_risk_rate='mean(at_risk_int)',
    groupby=['famrel']
).mark_line(point=True).encode(
    x=alt.X('famrel:O', title='Family Relationship Quality (1–5)'),
    y=alt.Y('at_risk_rate:Q', title='Proportion At-Risk', axis=alt.Axis(format='%')),
    tooltip=['famrel:O', alt.Tooltip('at_risk_rate:Q', format='.1%')]
).properties(
    width=600,
    height=400,
    title='Proportion At-Risk by Family Relationship Quality'
)
famrel_risk

alt.Chart(...)

In [25]:
dalc_risk = alt.Chart(df_ar).transform_aggregate(
    at_risk_rate='mean(at_risk_int)',
    groupby=['Dalc']
).mark_line(point=True).encode(
    x=alt.X('Dalc:O', title='Workday Alcohol Use (1–5)'),
    y=alt.Y('at_risk_rate:Q', title='Proportion At-Risk', axis=alt.Axis(format='%')),
    tooltip=['Dalc:O', alt.Tooltip('at_risk_rate:Q', format='.1%')]
).properties(
    width=600,
    height=400,
    title='Proportion At-Risk by Workday Alcohol Use'
)
dalc_risk

alt.Chart(...)

In [26]:
walc_risk = alt.Chart(df_ar).transform_aggregate(
    at_risk_rate='mean(at_risk_int)',
    groupby=['Walc']
).mark_line(point=True).encode(
    x=alt.X('Walc:O', title='Weekend Alcohol Use (1–5)'),
    y=alt.Y('at_risk_rate:Q', title='Proportion At-Risk', axis=alt.Axis(format='%')),
    tooltip=['Walc:O', alt.Tooltip('at_risk_rate:Q', format='.1%')]
).properties(
    width=600,
    height=400,
    title='Proportion At-Risk by Weekend Alcohol Use'
)
walc_risk

alt.Chart(...)

#### ***2. Predictive (Regression):***

In [39]:
def prob_log_loss(y_true, y_prob, eps=1e-15):
    y_prob = np.clip(y_prob, eps, 1 - eps)
    return log_loss(y_true, y_prob)

In [55]:
df_reg = pd.concat([mat, por], ignore_index=True)

df = df_reg.copy()

df["at_risk"] = (df["G3"] < 10).astype(int)

predictors = [
    "age", "absences", "failures", "famrel", "famsup", "internet", "schoolsup", "school",
    "Pstatus", "Medu", "Fedu", "address", "nursery", "goout", "Walc", "Dalc", "health"
]

X = pd.get_dummies(df[predictors], drop_first=True)
y = df["at_risk"].values

In [56]:
param_dist = {
    "logreg__C": np.logspace(-3, 3, 50)
}

In [57]:
param_grid = {
    "logreg__C": np.logspace(-3, 3, 25)
}

In [58]:
kf = KFold(n_splits=5, shuffle=True, random_state=42)

selected = []
remaining = X.columns.tolist()
results_logreg = []

previous_score = np.inf

for step in range(len(remaining)):
    best_feature = None
    best_score = np.inf

    for feature in remaining:
        trial_features = selected + [feature]
        X_trial = X[trial_features].values

        fold_scores = []

        for train_idx, val_idx in kf.split(X_trial):
            X_train_cv, X_val_cv = X_trial[train_idx], X_trial[val_idx]
            y_train_cv, y_val_cv = y[train_idx], y[val_idx]

            search = GridSearchCV(
                logreg_pipeline,
                param_grid=param_grid,
                scoring="neg_log_loss",
                cv=3,
                n_jobs=-1
            )

            search.fit(X_train_cv, y_train_cv)

            probs = search.best_estimator_.predict_proba(X_val_cv)[:, 1]
            fold_scores.append(prob_log_loss(y_val_cv, probs))

        mean_rmspe = np.mean(fold_scores)

        if mean_rmspe < best_score:
            best_score = mean_rmspe
            best_feature = feature

    if best_score >= previous_score:
        break

    selected.append(best_feature)
    remaining.remove(best_feature)
    previous_score = best_score

    results_logreg.append({
        "Step": step + 1,
        "Predictor Added": best_feature,
        "CV Log Loss": round(best_score, 4)
    })

In [59]:
results_df = pd.DataFrame(results_logreg)
results_df

Step Predictor Added  CV Log Loss
0     1        failures       0.4752
1     2       school_MS       0.4691
2     3        absences       0.4654
3     4     nursery_yes       0.4644
4     5           goout       0.4639
5     6   schoolsup_yes       0.4634
6     7       Pstatus_T       0.4630

In [52]:
print("Selected predictors (in order):")
print(selected)

print(f"Final cross-validated Log Loss: {previous_score:.4f}")

Selected predictors (in order):
['failures', 'absences', 'Medu', 'goout', 'famrel', 'Pstatus_T', 'Walc']
Final cross-validated Log Loss: 0.4719


In [60]:
final_predictors = [
    "failures",
    "school_MS",
    "absences",
    "nursery_yes",
    "goout",
    "schoolsup_yes",
    "Pstatus_T"
]

X_final = X[final_predictors]
y = df["at_risk"].values

In [61]:
final_model = Pipeline([
    ("scaler", StandardScaler()),
    ("logreg", LogisticRegression(
        penalty="l2",
        solver="liblinear",
        C=1.0,          # replace if you saved best C
        max_iter=1000
    ))
])

final_model.fit(X_final, y)

Pipeline(steps=[('scaler', StandardScaler()),
                ('logreg',
                 LogisticRegression(max_iter=1000, solver='liblinear'))])

In [62]:
coefs = final_model.named_steps["logreg"].coef_[0]

coef_table = pd.DataFrame({
    "Predictor": final_predictors,
    "Coefficient (log-odds)": coefs,
    "Odds Ratio": np.exp(coefs)
}).sort_values("Odds Ratio", ascending=False)

coef_table

Predictor  Coefficient (log-odds)  Odds Ratio
0       failures                0.716341    2.046929
1      school_MS                0.347684    1.415785
2       absences                0.260548    1.297641
4          goout                0.205306    1.227901
5  schoolsup_yes                0.155524    1.168270
3    nursery_yes                0.113141    1.119790
6      Pstatus_T                0.107447    1.113432

#### ***3. Inferential (Bootstrap):***

In [27]:
def bootstrap_mean_diff(group1, group2, boot=5000, random_state=42):
    rng = np.random.default_rng(random_state)
    diffs = []

    for _ in range(boot):
        boot1 = rng.choice(group1, size=len(group1), replace=True)
        boot2 = rng.choice(group2, size=len(group2), replace=True)
        diffs.append(np.mean(boot1) - np.mean(boot2))

    lower, upper = np.percentile(diffs, [2.5, 97.5])
    return np.mean(diffs), lower, upper

In [28]:
df_inf = pd.concat([mat, por], ignore_index=True)

In [29]:
comparisons = {
    "Family Relationship Quality (famrel ≥ 4 vs ≤ 3)": {
        "strong": df_inf["famrel"] >= 4,
        "weak":   df_inf["famrel"] <= 3
    },
    "Parental Cohabitation (Together vs Apart)": {
        "strong": df_inf["Pstatus"] == "T",
        "weak":   df_inf["Pstatus"] == "A"
    },
    "Family Educational Support (yes vs no)": {
        "strong": df_inf["famsup"] == "yes",
        "weak":   df_inf["famsup"] == "no"
    },
    "Going Out (goout ≥ 4 vs ≤ 3)": {
        "strong": df_inf["goout"] >= 4,
        "weak":   df_inf["goout"] <= 3
    },
    "Health Status (health ≥ 4 vs ≤ 3)": {
        "strong": df_inf["health"] >= 4,
        "weak":   df_inf["health"] <= 3
    },
    "Internet Access (yes vs no)": {
        "strong": df_inf["internet"] == "yes",
        "weak":   df_inf["internet"] == "no"
    },
    "Attended Nursery School (yes vs no)": {
        "strong": df_inf["nursery"] == "yes",
        "weak":   df_inf["nursery"] == "no"
    },
    "Address Type (Urban vs Rural)": {
        "strong": df_inf["address"] == "U",
        "weak":   df_inf["address"] == "R"
    },
    "School (GP vs MS)": {
        "strong": df_inf["school"] == "GP",
        "weak":   df_inf["school"] == "MS"
    },
    "Extra Educational Support   (yes vs no)": {
        "strong": df_inf["schoolsup"] == "yes",
        "weak":   df_inf["schoolsup"] == "no"
    }
}

In [30]:
results = []
for label, rule in comparisons.items():
    strong_vals = df_inf.loc[rule["strong"], "G3"]
    weak_vals   = df_inf.loc[rule["weak"], "G3"]

    mean_diff, ci_low, ci_high = bootstrap_mean_diff(strong_vals, weak_vals)
    
    results.append({
        "Comparison": label,
        "Mean Difference (Strong - Weak)": round(mean_diff, 2),
        "95% CI Low": round(ci_low, 2),
        "95% CI High": round(ci_high, 2),
        "Significant?": "Yes" if ci_low > 0 or ci_high < 0 else "No"
    })

In [31]:
results_df = pd.DataFrame(results)
results_df

Comparison  \
0  Family Relationship Quality (famrel ≥ 4 vs ≤ 3)   
1        Parental Cohabitation (Together vs Apart)   
2           Family Educational Support (yes vs no)   
3                     Going Out (goout ≥ 4 vs ≤ 3)   
4                Health Status (health ≥ 4 vs ≤ 3)   
5                      Internet Access (yes vs no)   
6              Attended Nursery School (yes vs no)   
7                    Address Type (Urban vs Rural)   
8                                School (GP vs MS)   
9          Extra Educational Support   (yes vs no)   

   Mean Difference (Strong - Weak)  95% CI Low  95% CI High Significant?  
0                             0.65        0.08         1.23          Yes  
1                            -0.37       -1.05         0.33           No  
2                             0.11       -0.38         0.60           No  
3                            -0.94       -1.44        -0.45          Yes  
4                            -0.32       -0.80         0.15           No  
5                             1.02        0.44         1.62          Yes  
6                             0.39       -0.19         0.98           No  
7                             1.02        0.49         1.56          Yes  
8                             1.11        0.59         1.65          Yes  
9                            -0.96       -1.51        -0.42          Yes